In [0]:
import subprocess

try:
    result = subprocess.run(['pip', 'install', 'azure-storage-file-datalake', 'databricks-cli', 'fernet'], check=True, capture_output=True, text=True)
    print("Installation successful!")
except subprocess.CalledProcessError as e:
    # print("Error during installation:", e.stderr)
    raise e


Installation successful!


In [0]:
dbutils.library.restartPython()

In [0]:
ACCOUNT_KEY = dbutils.secrets.get(scope = "storage-account-secrets", key = "databricks-account-key")
ACCOUNT_NAME = dbutils.secrets.get(scope = "storage-account-secrets", key = "databricks-account-name")

In [0]:
from pyspark.storagelevel import StorageLevel
from pyspark.sql.functions import *
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, FloatType, DoubleType
from azure.storage.filedatalake import DataLakeServiceClient, FileSystemClient, DataLakeFileClient
from pyspark.sql import Row
import json
from cryptography.fernet import Fernet, InvalidToken

In [0]:
CONNECTION_STRING = f"DefaultEndpointsProtocol=https;AccountName={ACCOUNT_NAME};AccountKey={ACCOUNT_KEY};EndpointSuffix=core.windows.net"


# Initialize DataLakeServiceClient for Azure Data Lake Storage Gen2
data_lake_service_client = DataLakeServiceClient.from_connection_string(CONNECTION_STRING)

# Name of the filesystem (similar to container) where files are stored
file_system_name = "swiggydataset"


def download_and_parse_json(file_system_name, file_path):
    file_client = data_lake_service_client.get_file_system_client(file_system_name).get_file_client(file_path)
    try:
        # Download the JSON data as bytes
        file_data = file_client.download_file().readall()
        
        # Decode the bytes to a string and load it as JSON
        json_data = json.loads(file_data.decode('utf-8'))
        
        print("JSON data successfully retrieved and parsed")
        return json_data
    except Exception as e:
        print(f"Failed to download and parse JSON: {e}")
        raise e
        return None


try:
    # Attempt to download and parse the JSON data
    data = download_and_parse_json("swiggydataset", "main/bronze/swiggy.json")
    if data:
        print("Fetch completed")
    else:
        print("No data fetched")
except Exception as e:
    raise e
    print(f"An error occurred in the main block: {e}")
   

JSON data successfully retrieved and parsed
Fetch completed


In [0]:
records_restaurant = []
records_menu = []
 
# Loop through the top-level cities
for city_name, city_data in data.items():
    # If the city has sub-areas (nested cities), loop through them
    if isinstance(city_data, dict) and 'restaurants' in city_data:
        # No sub-area: directly process the city
        full_city_name = city_name
 
        # Loop through restaurants in the city
        for restaurant_id, restaurant_data in city_data.get('restaurants', {}).items():
            records_restaurant.append({
                'Restaurant_ID': restaurant_id,
                'Restaurant_Name': restaurant_data.get('name'),
                'City': full_city_name,
                'Rating': restaurant_data.get('rating'),
                'Rating_Count': restaurant_data.get('rating_count'),
                'Cost': restaurant_data.get('cost'),
                'Cuisine': restaurant_data.get('cuisine'),
                'Lic_No': restaurant_data.get('lic_no'),
                'Link': restaurant_data.get('link'),
                'Address': restaurant_data.get('address'),
            })
 
            # Loop through menu categories for the current restaurant
            for category, items in restaurant_data.get('menu', {}).items():
                # Loop through items in each category
                for item_name, item_data in items.items():
                    records_menu.append({
                        'Restaurant_ID': restaurant_id,
                        'Category': category,
                        'Item_Name': item_name,
                        'Price': item_data.get('price'),
                        'Veg_or_Non_Veg': item_data.get('veg_or_non_veg'),
                    })
 
    # If the city has sub-areas (nested cities), process each sub-area
    elif isinstance(city_data, dict):
        for sub_area_name, sub_area_data in city_data.items():
            full_city_name = f"{sub_area_name},{city_name}"
 
            # Loop through restaurants in the sub-area
            for restaurant_id, restaurant_data in sub_area_data.get('restaurants', {}).items():
                records_restaurant.append({
                    'Restaurant_ID': restaurant_id,
                    'Restaurant_Name': restaurant_data.get('name'),
                    'City': full_city_name,
                    'Rating': restaurant_data.get('rating'),
                    'Rating_Count': restaurant_data.get('rating_count'),
                    'Cost': restaurant_data.get('cost'),
                    'Cuisine': restaurant_data.get('cuisine'),
                    'Lic_No': restaurant_data.get('lic_no'),
                    'Link': restaurant_data.get('link'),
                    'Address': restaurant_data.get('address'),
                })
 
                # Loop through menu categories for the current restaurant
                for category, items in restaurant_data.get('menu', {}).items():
                    # Loop through items in each category
                    for item_name, item_data in items.items():
                        records_menu.append({
                            'Restaurant_ID': restaurant_id,
                            'Category': category,
                            'Item_Name': item_name,
                            'Price': item_data.get('price'),
                            'Veg_or_Non_Veg': item_data.get('veg_or_non_veg'),
                        })
 
# Convert to Spark DataFrames
df_restaurant = spark.createDataFrame(records_restaurant)
df_menu = spark.createDataFrame(records_menu)
 
# Show the results (optional)
# df_restaurant.show(truncate=False)
# df_menu.show(truncate=False)
 
 

seperate df

In [0]:
df_restaurant = df_restaurant.repartition(10)

# Shape of data

In [0]:
df_restaurant.count()

181404

In [0]:
len(df_restaurant.columns)

10

In [0]:
# df_restaurant.select('City').distinct().count()

# Handle Duplicates

In [0]:

restaurant_ids = df_restaurant.groupBy("Restaurant_ID").count().filter(col("count") > 1).select("Restaurant_ID")
restaurant_ids.count()

19530

In [0]:
df_restaurant.groupBy(['Restaurant_ID','Restaurant_Name','Address']).count().filter(col("count") > 1).count()

6796

In [0]:
df_restaurant_cleaned = df_restaurant.drop_duplicates(['Restaurant_ID'])

In [0]:
# df_restaurant_cleaned.count()

In [0]:
df_restaurant_cleaned.groupBy(['Restaurant_ID','Restaurant_Name','Address']).count().filter(col("count") > 1).count()

0

In [0]:
df_restaurant_cleaned.groupBy("Restaurant_ID").count().filter(col("count") > 1).count()

0

In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.drop_duplicates(['Restaurant_ID'])


In [0]:
df_restaurant_cleaned.persist(StorageLevel.DISK_ONLY)

DataFrame[Address: string, City: string, Cost: string, Cuisine: string, Lic_No: string, Link: string, Rating: string, Rating_Count: string, Restaurant_ID: string, Restaurant_Name: string]

# Handle Null Values

In [0]:
df_restaurant_cleaned.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_restaurant_cleaned.columns]).show()

+-------+----+-----+-------+------+----+------+------------+-------------+---------------+
|Address|City| Cost|Cuisine|Lic_No|Link|Rating|Rating_Count|Restaurant_ID|Restaurant_Name|
+-------+----+-----+-------+------+----+------+------------+-------------+---------------+
|  18018|   0|18018|  18018| 18018|   0|     0|       18018|            0|              0|
+-------+----+-----+-------+------+----+------+------------+-------------+---------------+



In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.dropna()

## Clean Data

Remove Special characters from Cost Column

In [0]:


df_restaurant_cleaned = df_restaurant_cleaned.withColumn(
    'Cost',
    when(col('Cost') == 'NA', None)  # Replace 'NA' with null
    .otherwise(regexp_replace(col('Cost'), '[^0-9]', ''))  # Clean and cast to double
)

city_mean_cost = df_restaurant_cleaned.groupBy('City').agg(
    avg('Cost').alias('Mean_Cost')
)


df_with_mean = df_restaurant_cleaned.join(city_mean_cost, on='City', how='left')

df_restaurant_cleaned = df_with_mean.withColumn(
    'Cost',
    round(coalesce(col('Cost'), col('Mean_Cost')), 2) 
).drop('Mean_Cost')


In [0]:
df_restaurant_cleaned.select('Cost').distinct().show()

+------+
|  Cost|
+------+
| 299.0|
|248.44|
| 650.0|
| 249.0|
| 800.0|
| 280.0|
| 350.0|
|1600.0|
| 380.0|
|  80.0|
| 120.0|
| 250.0|
| 300.0|
| 270.0|
| 225.0|
| 700.0|
| 220.0|
| 149.0|
| 340.0|
| 349.0|
+------+
only showing top 20 rows



Cleaning Rating_count column

In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.withColumn(
    'Rating_count',
    when(
        col('Rating_count').rlike('^\\d+\\+ ratings$'), 
        regexp_replace(col('Rating_count'), '\\+ ratings', '').cast('int')
    )
    .when(
        col('Rating_count').rlike('^\\d+K\\+ ratings$'),
        (regexp_replace(col('Rating_count'), 'K\\+ ratings', '').cast('double') * 1000).cast('int')
    )
    .when(
        col('Rating_count') == 'NA', 
        0
    )
    .when(
        col('Rating_count') == 'Too Few Ratings', 
        0
    )
    .otherwise(0)
    .cast('int') 
)

In [0]:
df_restaurant_cleaned.select('Rating_count').distinct().show()

+------------+
|Rating_count|
+------------+
|          20|
|         500|
|         100|
|        1000|
|          50|
|           0|
|        5000|
|       10000|
+------------+



Clean NA values

In [0]:
df_restaurant_cleaned.printSchema()

root
 |-- City: string (nullable = true)
 |-- Address: string (nullable = true)
 |-- Cost: double (nullable = true)
 |-- Cuisine: string (nullable = true)
 |-- Lic_No: string (nullable = true)
 |-- Link: string (nullable = true)
 |-- Rating: string (nullable = true)
 |-- Rating_count: integer (nullable = true)
 |-- Restaurant_ID: string (nullable = true)
 |-- Restaurant_Name: string (nullable = true)



In [0]:
df_restaurant_cleaned.select([sum(when(col(c) == 'NA', 1).otherwise(0).cast('int')).alias(c) for c in df_restaurant_cleaned.columns]).show()

+----+-------+----+-------+------+----+------+------------+-------------+---------------+
|City|Address|Cost|Cuisine|Lic_No|Link|Rating|Rating_count|Restaurant_ID|Restaurant_Name|
+----+-------+----+-------+------+----+------+------------+-------------+---------------+
|   0|      0|   0|     13|   138|   0|     0|           0|            0|              0|
+----+-------+----+-------+------+----+------+------------+-------------+---------------+



In [0]:
df_restaurant_cleaned.filter(col('Restaurant_Name') == 'NA').display()

City Address Cost Cuisine Lic_No Link Rating Rating_count Restaurant_ID Restaurant_Name Dwarka,Delhi NA 306.12 NA NA https://www.swiggy.com/restaurants/taco-bell-dwarka-delhi-34635 NA 0 34635 NA Viman Nagar,Pune NA 313.32 NA NA https://www.swiggy.com/restaurants/the-hidden-leaf-viman-nagar-pune-540585 NA 0 540585 NA Ichalkaranji NA 182.86 NA NA https://www.swiggy.com/restaurants/dominos-pizza-fortune-plaza-kolhapur-rajwada-ichalkaranji-98602 NA 0 98602 NA Rohtak NA 247.81 NA NA https://www.swiggy.com/restaurants/daily-delights-rohtak-city-rohtak-535264 NA 0 535264 NA George Town,Chennai NA 277.41 NA NA https://www.swiggy.com/restaurants/meet-my-bread-portuguese-church-street-george-town-chennai-140189 NA 0 140189 NA Kurukshetra NA 226.47 NA NA https://www.swiggy.com/restaurants/maan-hotel-air-colony-kurukshetra-391389 NA 0 391389 NA Raj Nagar,Noida NA 277.35 NA NA https://www.swiggy.com/restaurants/cinch-restaurant-and-lounge-raj-nagar-noida-71898 NA 0 71898 NA Mahalaxmi Malabar Hill,Mumbai NA 409.86 NA NA https://www.swiggy.com/restaurants/theobroma-breach-candy-mahalaxmi-area-mumbai-6621 NA 0 6621 NA Vasai,Mumbai NA 313.7 NA NA https://www.swiggy.com/restaurants/slay-coffee-vasai-vasai-west-mumbai-247077 NA 0 247077 NA Banjara Hills,Hyderabad NA 361.03 NA NA https://www.swiggy.com/restaurants/bowlsome-banjara-hills-hyderabad-219713 NA 0 219713 NA Faridabad NA 310.7 NA NA https://www.swiggy.com/restaurants/the-belgian-waffle-co-sector-15-faridabad-54790 NA 0 54790 NA Bhosari,Pune NA 271.4 NA NA https://www.swiggy.com/restaurants/the-biryani-life-near-indrayani-nagar-bhosari-pune-191319 NA 0 191319 NA Kaithal NA 218.87 NA NA https://www.swiggy.com/restaurants/tringrill-vivek-nagar-old-city-kaithal-361450 NA 0 361450 NA Gomti Nagar,Lucknow NA 272.17 NA NA https://www.swiggy.com/restaurants/dezzerts-vivek-khand-gomti-nagar-lucknow-59939 NA 0 59939 NA North-goa NA 479.39 NA NA https://www.swiggy.com/restaurants/zwe-by-golden-eye-baga-calangute-central-goa-511401 NA 0 511401 NA Rohini,Delhi NA 277.96 NA NA https://www.swiggy.com/restaurants/chef-brothers-shawarma-roll-community-center-sec-9-rohini-delhi-167737 NA 0 167737 NA Bhilai NA 231.88 NA NA https://www.swiggy.com/restaurants/jfc-namo-nehru-nagar-bhilai-552729 NA 0 552729 NA Greater Mohali,Chandigarh NA 242.31 NA NA https://www.swiggy.com/restaurants/5-tara-greater-mohali-chandigarh-397961 NA 0 397961 NA Ajmer NA 265.34 NA NA https://www.swiggy.com/restaurants/coffo-holic-india-motor-circle-hathi-bhata-ajmer-113550 NA 0 113550 NA Haridwar NA 220.53 NA NA https://www.swiggy.com/restaurants/the-8-planets-cafe-and-restaurant-karol-bagh-shivalik-nagar-haridwar-532864 NA 0 532864 NA Kurukshetra NA 226.47 NA NA https://www.swiggy.com/restaurants/khanna-fast-food-sector-7-sector-8-kurukshetra-170800 NA 0 170800 NA Ichalkaranji NA 182.86 NA NA https://www.swiggy.com/restaurants/bharat-biryani-city-jawaharnagar-ichalkaranji-183544 NA 0 183544 NA Amreli NA 152.96 NA NA https://www.swiggy.com/restaurants/rangoli-ice-cream-amreli-town-amreli-287875 NA 0 287875 NA Aliganj,Lucknow NA 238.99 NA NA https://www.swiggy.com/restaurants/kathi-castle-aliganj-lucknow-61730 NA 0 61730 NA Satara NA 224.35 NA NA https://www.swiggy.com/restaurants/rajdhani-pavbhaji-and-ice-cream-satara-city-satara-256827 NA 0 256827 NA Bhopal NA 257.88 NA NA https://www.swiggy.com/restaurants/food-n-fry-jahangirabad-bhopal-440842 NA 0 440842 NA Shivamogga NA 241.43 NA NA https://www.swiggy.com/restaurants/bakers-bowl-durgigudi-central-mall-circle-shivamogga-116615 NA 0 116615 NA Gwalior NA 249.83 NA NA https://www.swiggy.com/restaurants/b-k-bakery-lashkar-gola-ka-mandir-gwalior-190021 NA 0 190021 NA Kamothe,Mumbai NA 287.92 NA NA https://www.swiggy.com/restaurants/baskin-robbins-fc-panvel-mumbai-372024 NA 0 372024 NA Bhilwara NA 250.2 NA NA https://www.swiggy.com/restaurants/prince-bakers-azad-nagar-bhilwara-159446 NA 0 159446 NA West Chd,Chandigarh NA 259.01 NA NA https://www.swiggy.com/restaurants/franks-fried-chic

In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.filter(col('Restaurant_Name') != 'NA')

In [0]:
# df_restaurant_cleaned = df_restaurant_cleaned.filter(col('Cuisine') != 'NA')

Remove Unwanted columns

In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.drop('City_Link')

## Schema Refinement

In [0]:
df_restaurant_cleaned.printSchema()

root
 |-- City: string (nullable = true)
 |-- Address: string (nullable = true)
 |-- Cost: double (nullable = true)
 |-- Cuisine: string (nullable = true)
 |-- Lic_No: string (nullable = true)
 |-- Link: string (nullable = true)
 |-- Rating: string (nullable = true)
 |-- Rating_count: integer (nullable = true)
 |-- Restaurant_ID: string (nullable = true)
 |-- Restaurant_Name: string (nullable = true)



In [0]:

new_schema = StructType([
    StructField("Address", StringType(), True),
    StructField("City", StringType(), True),
    StructField("Cost", DoubleType(), True),              
    StructField("Cuisine", StringType(), True),
    StructField("Lic_No", StringType(), True),
    StructField("Rating", DoubleType(), True),             
    StructField("Rating_count", IntegerType(), True),     
    StructField("Restaurant_ID", IntegerType(), True),    
    StructField("Restaurant_Name", StringType(), True)
])

df_restaurant_cleaned = df_restaurant_cleaned.select(
    [col(field.name).cast(field.dataType) for field in new_schema.fields]
)


In [0]:
df_restaurant_cleaned.printSchema()

root
 |-- Address: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Cost: double (nullable = true)
 |-- Cuisine: string (nullable = true)
 |-- Lic_No: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Rating_count: integer (nullable = true)
 |-- Restaurant_ID: integer (nullable = true)
 |-- Restaurant_Name: string (nullable = true)



In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.fillna({'Rating_count': 0})

In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.fillna({'Rating': 0})

In [0]:
# df_restaurant_cleaned.display()

In [0]:
df_restaurant_cleaned.count()

148476

# License Encryption

In [0]:
# key = Fernet.generate_key()

In [0]:
enc_dec_key = dbutils.secrets.get(scope="storage-account-secrets", key="databrick-enc-key")


def encrypt_val(clear_text, master_key):
    if not clear_text or clear_text == "NA":  
        return clear_text  
    try:
        f = Fernet(master_key)
        clear_text_b = bytes(clear_text, 'utf-8')
        cipher_text = f.encrypt(clear_text_b)
        return cipher_text.decode('ascii')
    except Exception as e:
        print(f"Encryption error: {e}") 
        return None

def decrypt_val(cipher_text, master_key):
    if not cipher_text or cipher_text == "NA":  
        return cipher_text  
    try:
        f = Fernet(master_key)
        clear_val = f.decrypt(cipher_text.encode()).decode()
        return clear_val
    except InvalidToken:
        print(f"Decryption error: Invalid Token for input {cipher_text}")  
        return None
    except Exception as e:
        print(f"Decryption error: {e}") 
        return None

encrypt_val_udf = udf(lambda x: encrypt_val(x, enc_dec_key), StringType())
decrypt_val_udf = udf(lambda x: decrypt_val(x, enc_dec_key), StringType())


In [0]:
df_restaurant_cleaned = df_restaurant_cleaned.withColumn('Lic_No', regexp_replace(col('Lic_No'), 'license', 'NA'))

In [0]:
df_restaurant_enc = df_restaurant_cleaned.withColumn("Lic_No",
    when(col("Lic_No") != "NA", encrypt_val_udf(col("Lic_No").cast("string")))  
    .otherwise(col("Lic_No"))  
)

In [0]:
df_restaurant_cleaned.unpersist()

DataFrame[Address: string, City: string, Cost: double, Cuisine: string, Lic_No: string, Rating: double, Rating_count: int, Restaurant_ID: int, Restaurant_Name: string]

# Menu

In [0]:
df_menu.persist(StorageLevel.DISK_ONLY)

DataFrame[Category: string, Item_Name: string, Price: string, Restaurant_ID: string, Veg_or_Non_Veg: string]

In [0]:
# df_menu = df_menu.repartition(10,'Restaurant_ID')

In [0]:
df_menu.count()

13379782

In [0]:
len(df_menu.columns)

5

## Handle Duplicates

In [0]:
df_menu.select("Restaurant_ID") \
    .groupBy("Restaurant_ID") \
    .count() \
    .filter(col("count") > 1) \
    .display()

Restaurant_ID count 161396 65 186264 127 554195 254 426191 28 556732 60 100010 230 505024 29 446079 29 494244 53 51676 201 572049 28 439917 215 531979 113 372444 47 71627 64 474559 50 506213 118 327548 12 479615 55 555061 19 580551 82 297449 90 338514 2 535544 59 539630 22 58819 160 577511 92 238446 22 517254 44 552172 15 238564 27 188263 41 207330 42 147244 61 579482 20 562271 37 312177 206 447682 86 568222 127 131033 80 475197 43 412586 131 362772 44 452448 35 256543 104 229171 44 349822 202 377792 151 491658 28 554792 102 286156 12 430085 78 26082 72 336531 84 387590 77 26005 65 422448 33 346181 43 233815 32 411129 56 562758 37 434492 50 396388 56 542026 10 580770 20 495594 53 58197 151 566996 31 321571 58 404987 166 476186 25 551990 115 513652 116 9586 109 259367 34 570728 44 441020 86 327831 43 558700 28 554284 12 10096 339 531404 29 551479 6 377555 15 217048 210 486979 82 389897 53 527376 77 530405 191 179486 15 516553 14 412576 53 446993 96 406094 168 437369 89 564446 61 554764 13 23843 83 247256 59 457924 88 62912 98 372616 66 567502 150 442129 5 336437 45 508647 28 337220 10 414329 36 418913 113 414295 85 375150 342 550401 24 286258 79 488782 107 502620 174 396750 73 3210 413 408270 78 556995 84 496227 83 228411 3 243698 89 369344 224 194703 9 504372 119 194850 25 191714 3 187223 179 388849 162 439051 16 168155 218 525494 15 554630 37 206495 32 428986 209 448710 54 283095 58 77339 254 295303 35 560145 163 144656 313 327654 72 565747 378 274400 340 438129 164 461143 477 478552 251 494277 78 59318 306 93893 400 355412 233 456057 111 553835 164 570592 88 500903 22 556677 16 510394 166 511472 126 556710 16 509792 26 476559 46 529593 98 429517 87 566706 78 342580 109 503075 83 474759 157 74468 100 212214 78 515874 83 567163 13 541160 87 414154 7 425451 43 18130 88 380451 125 57868 66 352042 25 553470 141 250006 103 103123 69 57112 55 508840 14 63738 250 276129 52 563113 30 240472 247 227447 14 452827 20 263145 132 486298 69 561519 52 46534 190 573256 18 48738 258 527628 43 514838 45 388645 106 515937 272 492618 292 445770 50 437229 74 67874 185 129219 66 488972 27 190512 188 127111 226 576806 118 526887 58 547630 52 303193 144 488488 2 420648 57 330927 80 59431 146 415789 177 323011 76 91767 137 467021 164 94345 40 64054 62 243905 187 139640 120 469329 88 570312 74 166903 107 306319 74 475118 80 518856 95 483299 139 225958 91 502147 59 557539 19 441375 48 378860 52 536608 73 106331 100 510188 23 77291 384 560413 22 262364 11 170995 7 393425 6 134699 106 469498 189 208797 71 436740 14 490881 43 444875 147 502663 21 554163 16 375928 67 565032 38 429444 87 512476 11 133181 135 1669 137 387576 95 259012 16 516643 50 151213 49 41313 144 523191 73 274914 100 383148 120 50556 70 303852 59 347840 88 531747 27 263608 62 568814 120 466845 73 554067 23 523313 41 66603 361 413475 74 282344 74 367030 92 414886 61 470728 114 295573 55 570220 66 337374 116 349875 99 450679 121 550235 51 354050 79 458541 31 423247 35 461504 89 133189 98 404035 140 328816 39 324585 158 543521 11 333584 25 538415 38 502865 200 517142 26 524140 47 446297 174 368715 12 47877 141 359645 50 508993 57 410299 29 482607 38 3368 313 440688 26 491592 48 31330 23 440128 98 481097 26 217427 135 494395 32 106014 117 530238 46 373630 75 457345 65 18386 89 344249 72 490599 82 552723 51 20256 212 46879 270 236414 92 421841 153 446286 69 345872 83 500137 69 538308 56 566670 20 542006 28 388632 37 488779 114 477999 45 337566 36 219460 73 318481 119 111349 222 493464 114 134323 297 101167 83 467586 30 336564 12 436695 196 192219 118 538780 48 165835 89 578539 174 531260 104 229818 95 504353 79 436636 43 548267 79 165366 128 490028 5 464207 35 10603 81 448543 228 223708 131 417003 63 195481 97 340262 87 488094 70 406041 11 53791 146 524707 19 357246 111 544605 156 438326 177 490100 137 336613 77 379425 22 40353 178 367806 103 576127 43 293899 176 327915 250 400151 114 88150 170 189037 32 185690 136 304454 69 380114 58 537631 59 463050 153 385306 204 576702 82 376487 187 49381

In [0]:
df_menu_cleaned = df_menu.drop_duplicates(['Restaurant_ID','Category'])

In [0]:
df_menu.unpersist()

DataFrame[Category: string, Item_Name: string, Price: string, Restaurant_ID: string, Veg_or_Non_Veg: string]

In [0]:
df_menu_cleaned.count()

1375657

In [0]:
# df_menu_cleaned = df_menu_cleaned.repartition(10,'Restaurant_ID')
df_menu_cleaned.persist(StorageLevel.DISK_ONLY)

DataFrame[Category: string, Item_Name: string, Price: string, Restaurant_ID: string, Veg_or_Non_Veg: string]

In [0]:
# df_menu_cleaned.count()

## Handle Null values

In [0]:
df_menu_cleaned.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_menu_cleaned.columns]).show()

+--------+---------+-----+-------------+--------------+
|Category|Item_Name|Price|Restaurant_ID|Veg_or_Non_Veg|
+--------+---------+-----+-------------+--------------+
|       0|        0|    0|            0|             0|
+--------+---------+-----+-------------+--------------+



In [0]:
df_menu_cleaned.dropna()

DataFrame[Category: string, Item_Name: string, Price: string, Restaurant_ID: string, Veg_or_Non_Veg: string]

## Clean NA values

In [0]:
df_menu_cleaned.select([sum(when(col(c) == 'NA', 1).otherwise(0).cast('int')).alias(c) for c in df_menu_cleaned.columns]).show()


Category Item_Name Price Restaurant_ID Veg_or_Non_Veg 0 0 0 0 0

In [0]:
df_menu_cleaned = df_menu_cleaned.filter((col('Item_Name') != 'NA') | (col('Restaurant_ID') != 'NA'))

### Refine Schema

In [0]:
menu_schema = StructType([
    StructField("Category", StringType(), True),
    StructField("Item_Name", StringType(), True),
    StructField("Price", FloatType(), True),               
    StructField("Restaurant_ID", StringType(), True),
    StructField("Veg_or_Non_Veg", StringType(), True)
])

# Assuming df_restaurant is the DataFrame you are working with
df_menu_cleaned = df_menu_cleaned.select(
    [col(field.name).cast(field.dataType) for field in menu_schema.fields]
)

In [0]:
df_grouped = df_menu_cleaned.groupBy('Restaurant_ID').agg(
    collect_list(
        struct('Category', 'Item_Name', 'Price', 'Restaurant_ID', 'Veg_or_Non_Veg')
    ).alias('Menu_Items')
)

In [0]:
df_menu_cleaned.unpersist()

DataFrame[Category: string, Item_Name: string, Price: float, Restaurant_ID: string, Veg_or_Non_Veg: string]

In [0]:
# df_grouped.display()

In [0]:
df_grouped.printSchema()

root
 |-- Restaurant_ID: string (nullable = true)
 |-- Menu_Items: array (nullable = false)
 |    |-- element: struct (containsNull = false)
 |    |    |-- Category: string (nullable = true)
 |    |    |-- Item_Name: string (nullable = true)
 |    |    |-- Price: float (nullable = true)
 |    |    |-- Restaurant_ID: string (nullable = true)
 |    |    |-- Veg_or_Non_Veg: string (nullable = true)



In [0]:
df_joined = df_restaurant_enc.join(df_grouped, on='Restaurant_ID', how='left')

In [0]:
# df_joined.display()

In [0]:
# df_joined.count()

## Silver Delta table

### Add Timestamp column

In [0]:
df_joined = df_joined.withColumn("Updated_Time", current_timestamp())

In [0]:
df_joined.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_joined.columns]).show()


+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+
|Restaurant_ID|Address|City|Cost|Cuisine|Lic_No|Rating|Rating_count|Restaurant_Name|Menu_Items|Updated_Time|
+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+
|            0|      0|   0|   0|      0|     0|     0|           0|              0|      1412|           0|
+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+



In [0]:
df_joined.display()

Restaurant_ID Address City Cost Cuisine Lic_No Rating Rating_count Restaurant_Name Menu_Items Updated_Time 211 Tandoor Hut, 477, KHB Colony, 5th Block, Koramangala Koramangala,Bangalore 300.0 Biryani,Chinese gAAAAABne6cdvoboAgoGADe85YyEuOQR-j_fNWlyBdmCSdKJS_hZdyvnBZMuyVNTDZ3Ljq19zmQfW8-bpy3-PnG-iQEyAhwIXw== 4.3 100 Tandoor Hut List(List(Starters, Chicken Kalmi Kebab(half), 205.0, 211, Non-veg), List(Recommended, Tandoor Chicken (half), 255.0, 211, Non-veg), List(Chinese Main Course, Chicken Fried Rice, 180.0, 211, Non-veg), List(Beverages, Coca Cola, 75.0, 211, Veg), List(Salads, Green Salad, 65.0, 211, Veg), List(Main Course, Paneer Amritsar, 230.0, 211, Veg), List(Biryani And Rice, Chicken Dum Biryani Special, 255.0, 211, Non-veg), List(Family Binge Combos, Chicken Dum Biryani + Chicken Malai Kebab(5Pcs), 405.0, 211, Non-veg), List(Indian Breads, Butter Roti, 50.0, 211, Veg), List(Soups, Cream of Veg Soup, 95.0, 211, Veg), List(Accompaniments, Roasted Papad, 35.0, 211, Veg)) 2025-01-06T09:48:57.213Z 218 Anand Sweets and Savouries, 143/A, 60 Feet Road, 5th Block, Koramangala, Bengaluru, Karnataka 560034 Koramangala,Bangalore 300.0 Sweets,Snacks gAAAAABne6cW6jzkCloMkezyMdH6vQmxU7M621v3III4olUDQexgvcxrEnIXpbk5h40-vng67pYmk6plxOETSSllZCP8EwaC0g== 4.4 1000 Anand Sweets and Savouries List(List(Namkeen Packs, Rice Kodubale, 80.36, 218, Veg), List(Dry Fruits, Salted Kaju, 321.43, 218, Veg), List(Canned Sweets, Rasgulla Tin Pack, 119.1, 218, Veg), List(Fresh Malai Paneer, Paneer, 138.1, 218, Veg), List(Fresh Snacks, Veg Patties (2 Pcs), 80.0, 218, Veg), List(Gift Hampers, Silver Moon Hamper, 3428.5, 218, Veg), List(Sugarfree Range, Sugar Free Soan Papdi, 171.43, 218, Veg), List(Makhana, Makhana Sour Cream And Onion, 125.0, 218, Veg), List(Purani Dilli Main Course, Paneer Paratha PD, 150.0, 218, Veg), List(Purani Dilli Special Chaats, Raj Kachori PD, 150.0, 218, Veg), List(Teatime Bites, Yellu Murukku, 116.07, 218, Veg), List(Desserts, Raj Bhog (2 Pcs), 85.71, 218, Veg), List(Main Course, Soya Chaap & Roomali Roti, 180.0, 218, Veg), List(Beverages, Kesar Badam Milk, 90.0, 218, Veg), List(Sweets, Navratan Laddu, 233.33, 218, Veg), List(Anand Special Sharbat, Thandai, 338.98, 218, Veg), List(Festive Specials, Teej Ki Pheni, 66.67, 218, Veg), List(Gift Packs, Turkish Baklawa Square Tin, 600.0, 218, Veg), List(Chips, Gujarathi Papdi, 80.35, 218, Veg), List(Namkeens, Wafer Mixture Pack, 116.07, 218, Veg), List(Indian Bakery, Fruit Cake Rusk, 142.8, 218, Veg)) 2025-01-06T09:48:57.213Z 223 Truffles, 93/A, Appek Building, 'A' Wing, 4th 'B' Cross, Koramangala Industrial Layout, 5th Block, Koramangala, Bangalore - 560 095 Koramangala,Bangalore 450.0 American,Continental gAAAAABne6cURELGNv8KlvCTWkdAYc83u9JzslgdoCvWxWoD1Da3KULcCcQf8rcrfCvANUWv7VFb3bTf6Aep7MBLIlfa8GtK4A== 4.4 5000 Truffles List(List(Pav, Mutton Kheema Pav, 247.62, 223, Non-veg), List(Burger, All American Veg Burger, 214.29, 223, Veg), List(Fries & Wedges, Classic Fries, 114.29, 223, Veg), List(Beverages, Black Currant Granita (400ML), 123.81, 223, Veg), List(Pizza, 3 Pepper & Sweet Corn Pizza [6 inch], 152.39, 223, Veg), List(Pasta, Aglio-Olio Pasta Veg, 204.77, 223, Veg), List(Truffles Special, Chocolate Lava Cake, 85.72, 223, Veg), List(Rice Bowl, Devil's Paneer Rice Bowl, 238.1, 223, Veg), List(Healthy Twist, 2 Bean & Grilled Vegetable Salad, 152.39, 223, Veg), List(Egg To Order, Fried Egg 3Pcs, 104.77, 223, Non-veg), List(Salad, Caesar Salad(Veg), 166.67, 223, Veg), List(Oriental, Fire & Spice With Rice(Veg), 276.2, 223, Veg), List(Full Cakes, Butterscotch 1/2kg, 428.58, 223, Non-veg), List(Sandwiches, Cheese S/W, 109.53, 223, Veg), List(Starters, All American Nachos Veg, 247.62, 223, Veg), List(Hot Dog, Chicken Hot Dog [Single], 133.34, 223, Non-veg), List(Add Ons, Mayo, 33.34, 223, Non-veg), List(Maincourse, Cottage Cheese Steak, 271.43, 223, Veg), List(Wraps, Mushroom & Cheese Wrap, 147.62, 223, Veg), List(Desserts, Macarons (6pcs), 285.72, 223, Non-veg), List(Submarine, Co

In [0]:
df_joined.count()

148476

In [0]:
len(df_joined.columns)

11

In [0]:
df_joined.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_joined.columns]).show()

+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+
|Restaurant_ID|Address|City|Cost|Cuisine|Lic_No|Rating|Rating_count|Restaurant_Name|Menu_Items|Updated_Time|
+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+
|            0|      0|   0|   0|      0|     0|     0|           0|              0|      1412|           0|
+-------------+-------+----+----+-------+------+------+------------+---------------+----------+------------+



In [0]:


agg_exprs = [
    sum(when(col(c) == 'NA', 1).otherwise(0)).alias(c)
    for c in df_joined.columns
    if not isinstance(df_joined.schema[c].dataType, ArrayType)
]

df_agg = df_joined.agg(*agg_exprs)
display(df_agg)

Restaurant_ID Address City Cost Cuisine Lic_No Rating Rating_count Restaurant_Name Updated_Time 0 0 0 0 0 12997 0 0 0 0

In [0]:
spark.conf.set(f"fs.azure.account.key.{ACCOUNT_NAME}.dfs.core.windows.net", ACCOUNT_KEY)
 

delta_table_path_final = f"abfss://swiggydataset@{ACCOUNT_NAME}.dfs.core.windows.net/main/silver/"

df_joined.write.format("delta").mode("append").save(delta_table_path_final)